In [490]:
import pandas as pd
import numpy as np
from tqdm import tqdm
from sklearn import model_selection
from sklearn.metrics import accuracy_score
import xgboost as xgb
import warnings
import matplotlib.pyplot as plt

warnings.filterwarnings('ignore')

#### TEAMS DATA

In [491]:
train_home_team_statistics_df = pd.read_csv('./Train_Data/train_home_team_statistics_df.csv', index_col=0)
train_away_team_statistics_df = pd.read_csv('./Train_Data/train_away_team_statistics_df.csv', index_col=0)

train_scores = pd.read_csv('./Target/Y_train.csv', index_col=0)

train_home = train_home_team_statistics_df.iloc[:,2:]
train_away = train_away_team_statistics_df.iloc[:,2:]

train_home.columns = 'HOME_' + train_home.columns
train_away.columns = 'AWAY_' + train_away.columns

train_data_teams =  pd.concat([train_home,train_away],join='inner',axis=1)
train_scores = train_scores.loc[train_data_teams.index]

train_data_teams = train_data_teams.replace({np.inf:np.nan,-np.inf:np.nan})

In [492]:
train_data_teams

HOME_TEAM_SHOTS_TOTAL_season_sum  HOME_TEAM_SHOTS_INSIDEBOX_season_sum  \
ID                                                                              
0                                   3.0                                   2.0   
1                                   6.0                                   8.0   
2                                   4.0                                   2.0   
3                                   7.0                                   5.0   
4                                   3.0                                   3.0   
...                                 ...                                   ...   
12298                               4.0                                   2.0   
12299                               4.0                                   2.0   
12300                               4.0                                   3.0   
12301                               2.0                                   NaN   
12302                               2.0                                   3.0   

       HOME_TEAM_SHOTS_OFF_TARGET_season_sum  \
ID                                             
0                                        5.0   
1                                        3.0   
2                                        5.0   
3                                        5.0   
4                                        2.0   
...                                      ...   
12298                                    3.0   
12299                                    3.0   
12300                                    5.0   
12301                                    1.0   
12302                                    1.0   

       HOME_TEAM_SHOTS_ON_TARGET_season_sum  \
ID                                            
0                                       2.0   
1                                       6.0   
2                                       2.0   
3                                       6.0   
4                                       3.0   
...                                     ...   
12298                                   4.0   
12299                                   1.0   
12300                                   3.0   
12301                                   1.0   
12302                                   2.0   

       HOME_TEAM_SHOTS_OUTSIDEBOX_season_sum  HOME_TEAM_PASSES_season_sum  \
ID                                                                          
0                                        1.0                          2.0   
1                                        5.0                          8.0   
2                                        8.0                          1.0   
3                                        6.0                          9.0   
4                                        4.0                          4.0   
...                                      ...                          ...   
12298                                    7.0                          4.0   
12299                                    5.0                          1.0   
12300                                    5.0                          1.0   
12301                                    NaN                          NaN   
12302                                    2.0                          3.0   

       HOME_TEAM_SUCCESSFUL_PASSES_season_sum  HOME_TEAM_SAVES_season_sum  \
ID                                                                          
0                                         2.0                         5.0   
1                                         7.0                        10.0   
2                                         1.0                         2.0   
3                                         9.0                         2.0   
4                                         3.0                         4.0   
...                                       ...                         ...   
12298                                     4.0                         3.0   
12299                

#### PLAYERS DATA

In [495]:
train_home_player_statistics_df = pd.read_csv('./Train_Data/train_home_player_statistics_df.csv', index_col=0)
train_away_player_statistics_df = pd.read_csv('./Train_Data/train_away_player_statistics_df.csv', index_col=0)

In [496]:
# defining irrelevant columns for each position
to_remove_from_all_positions = ['LEAGUE', 'TEAM_NAME', 'POSITION', 'PLAYER_NAME',
                                'PLAYER_CAPTAIN_season_sum', 'PLAYER_CAPTAIN_5_last_match_sum',
                                'PLAYER_CAPTAIN_season_average', 'PLAYER_CAPTAIN_5_last_match_average',
                                'PLAYER_CAPTAIN_season_std', 'PLAYER_CAPTAIN_5_last_match_std',
                                'PLAYER_PENALTIES_MISSES_season_sum', 'PLAYER_PENALTIES_SCORED_season_sum',
                                'PLAYER_PENALTIES_MISSES_season_average', 'PLAYER_PENALTIES_SCORED_season_average',
                                'PLAYER_PENALTIES_MISSES_season_std', 'PLAYER_PENALTIES_SCORED_season_std',
                                'PLAYER_PENALTIES_MISSES_5_last_match_sum', 'PLAYER_PENALTIES_SCORED_5_last_match_sum',
                                'PLAYER_PENALTIES_MISSES_5_last_match_average', 'PLAYER_PENALTIES_SCORED_5_last_match_average',
                                'PLAYER_PENALTIES_MISSES_5_last_match_std', 'PLAYER_PENALTIES_SCORED_5_last_match_std']

irrelevant_stats_defender = ['PLAYER_PENALTIES_SAVED_season_sum', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_sum',
                             'PLAYER_PENALTIES_SAVED_season_average', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_average',
                             'PLAYER_PENALTIES_SAVED_season_std', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_std',
                             'PLAYER_PENALTIES_SAVED_5_last_match_sum', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_sum',
                             'PLAYER_PENALTIES_SAVED_5_last_match_average', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_average',
                             'PLAYER_PENALTIES_SAVED_5_last_match_std', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_std']

irrelevant_stats_midfielder = ['PLAYER_PENALTIES_SAVED_season_sum', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_sum',
                             'PLAYER_PENALTIES_SAVED_season_average', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_average',
                             'PLAYER_PENALTIES_SAVED_season_std', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_std',
                             'PLAYER_PENALTIES_SAVED_5_last_match_sum', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_sum',
                             'PLAYER_PENALTIES_SAVED_5_last_match_average', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_average',
                             'PLAYER_PENALTIES_SAVED_5_last_match_std', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_std']

irrelevant_stats_attacker = ['PLAYER_PENALTIES_SAVED_season_sum', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_sum',
                             'PLAYER_PENALTIES_SAVED_season_average', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_average',
                             'PLAYER_PENALTIES_SAVED_season_std', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_season_std',
                             'PLAYER_PENALTIES_SAVED_5_last_match_sum', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_sum',
                             'PLAYER_PENALTIES_SAVED_5_last_match_average', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_average',
                             'PLAYER_PENALTIES_SAVED_5_last_match_std', 'PLAYER_GOALKEEPER_GOALS_CONCEDED_5_last_match_std']

to_remove_from_all_players = ['LEAGUE', 'TEAM_NAME', 'POSITION', 'PLAYER_NAME',
                                'PLAYER_CAPTAIN_season_sum', 'PLAYER_CAPTAIN_5_last_match_sum',
                                'PLAYER_CAPTAIN_season_average', 'PLAYER_CAPTAIN_5_last_match_average',
                                'PLAYER_CAPTAIN_season_std', 'PLAYER_CAPTAIN_5_last_match_std']

In [497]:
# filtering irrelevant columns for each position
train_home_attacker = train_home_player_statistics_df[train_home_player_statistics_df['POSITION'] == 'attacker'].drop(irrelevant_stats_attacker + to_remove_from_all_positions, axis=1)
train_home_defender = train_home_player_statistics_df[train_home_player_statistics_df['POSITION'] == 'defender'].drop(irrelevant_stats_defender + to_remove_from_all_positions, axis=1)
train_home_midfielder = train_home_player_statistics_df[train_home_player_statistics_df['POSITION'] == 'midfielder'].drop(irrelevant_stats_midfielder + to_remove_from_all_positions, axis=1)
train_home_goalkeeper = train_home_player_statistics_df[train_home_player_statistics_df['POSITION'] == 'goalkeeper'].drop(to_remove_from_all_positions, axis=1)

train_away_attacker = train_away_player_statistics_df[train_away_player_statistics_df['POSITION'] == 'attacker'].drop(irrelevant_stats_attacker + to_remove_from_all_positions, axis=1)
train_away_defender = train_away_player_statistics_df[train_away_player_statistics_df['POSITION'] == 'defender'].drop(irrelevant_stats_defender + to_remove_from_all_positions, axis=1)
train_away_midfielder = train_away_player_statistics_df[train_away_player_statistics_df['POSITION'] == 'midfielder'].drop(irrelevant_stats_midfielder + to_remove_from_all_positions, axis=1)
train_away_goalkeeper = train_away_player_statistics_df[train_away_player_statistics_df['POSITION'] == 'goalkeeper'].drop(to_remove_from_all_positions, axis=1)

# and for all team
train_home_all_players = train_home_player_statistics_df.drop(to_remove_from_all_players, axis=1)
train_away_all_players = train_away_player_statistics_df.drop(to_remove_from_all_players, axis=1)

In [498]:
# renaming columns
train_home_attacker.columns = [c.replace('PLAYER', 'ATTACKER') for c in train_home_attacker.columns]
train_home_midfielder.columns = [c.replace('PLAYER', 'MIDFIELDER') for c in train_home_midfielder.columns]
train_home_defender.columns = [c.replace('PLAYER', 'DEFENDER') for c in train_home_defender.columns]
train_home_goalkeeper.columns = [c.replace('PLAYER', 'GOALKEEPER') for c in train_home_goalkeeper.columns]

train_away_attacker.columns = [c.replace('PLAYER', 'ATTACKER') for c in train_away_attacker.columns]
train_away_midfielder.columns = [c.replace('PLAYER', 'MIDFIELDER') for c in train_away_midfielder.columns]
train_away_defender.columns = [c.replace('PLAYER', 'DEFENDER') for c in train_away_defender.columns]
train_away_goalkeeper.columns = [c.replace('PLAYER', 'GOALKEEPER') for c in train_away_goalkeeper.columns]

train_home_all_players.columns = [c.replace('PLAYER', 'ALL_PLAYERS') for c in train_home_all_players.columns]
train_away_all_players.columns = [c.replace('PLAYER', 'ALL_PLAYERS') for c in train_away_all_players.columns]

train_home_attacker.columns = 'HOME_' + train_home_attacker.columns
train_home_midfielder.columns = 'HOME_' + train_home_midfielder.columns
train_home_defender.columns = 'HOME_' + train_home_defender.columns
train_home_goalkeeper.columns = 'HOME_' + train_home_goalkeeper.columns

train_away_attacker.columns = 'AWAY_' + train_away_attacker.columns
train_away_midfielder.columns = 'AWAY_' + train_away_midfielder.columns
train_away_defender.columns = 'AWAY_' + train_away_defender.columns
train_away_goalkeeper.columns = 'AWAY_' + train_away_goalkeeper.columns

train_home_all_players.columns = 'HOME_' + train_home_all_players.columns
train_away_all_players.columns = 'AWAY_' + train_away_all_players.columns

In [499]:
# For each team, grouping the players that hold the same position
def weighted_avg(df, weight_column):
    weights = df[weight_column]
    value_columns = df.columns.to_list()
    value_columns.remove(weight_column)
    weighted_values = df[value_columns].multiply(weights, axis=0)
    return weighted_values.sum() / weights.sum()

# home data
train_home_attacker = train_home_attacker.groupby(train_home_attacker.index).apply(lambda x: weighted_avg(x, 'HOME_ATTACKER_MINUTES_PLAYED_season_sum'))
train_home_midfielder = train_home_midfielder.groupby(train_home_midfielder.index).apply(lambda x: weighted_avg(x, 'HOME_MIDFIELDER_MINUTES_PLAYED_season_sum'))
train_home_defender = train_home_defender.groupby(train_home_defender.index).apply(lambda x: weighted_avg(x, 'HOME_DEFENDER_MINUTES_PLAYED_season_sum'))
train_home_goalkeeper = train_home_goalkeeper.groupby(train_home_goalkeeper.index).apply(lambda x: weighted_avg(x, 'HOME_GOALKEEPER_MINUTES_PLAYED_season_sum'))
train_home_all_players = train_home_all_players.groupby(train_home_all_players.index).apply(lambda x: weighted_avg(x, 'HOME_ALL_PLAYERS_MINUTES_PLAYED_season_sum'))

# away data
train_away_attacker = train_away_attacker.groupby(train_away_attacker.index).apply(lambda x: weighted_avg(x, 'AWAY_ATTACKER_MINUTES_PLAYED_season_sum'))
train_away_midfielder = train_away_midfielder.groupby(train_away_midfielder.index).apply(lambda x: weighted_avg(x, 'AWAY_MIDFIELDER_MINUTES_PLAYED_season_sum'))
train_away_defender = train_away_defender.groupby(train_away_defender.index).apply(lambda x: weighted_avg(x, 'AWAY_DEFENDER_MINUTES_PLAYED_season_sum'))
train_away_goalkeeper = train_away_goalkeeper.groupby(train_away_goalkeeper.index).apply(lambda x: weighted_avg(x, 'AWAY_GOALKEEPER_MINUTES_PLAYED_season_sum'))
train_away_all_players = train_away_all_players.groupby(train_away_all_players.index).apply(lambda x: weighted_avg(x, 'AWAY_ALL_PLAYERS_MINUTES_PLAYED_season_sum'))

In [500]:
# filling missing rows with NaN
# (these missing rows are due to players with no mentioned POSITION in the .csv file)
home_attacker_indexes = train_home_attacker.index.to_list()
home_midfielder_indexes = train_home_midfielder.index.to_list()
home_defender_indexes = train_home_defender.index.to_list()
home_goalkeeper_indexes = train_home_goalkeeper.index.to_list()

away_attacker_indexes = train_away_attacker.index.to_list()
away_midfielder_indexes = train_away_midfielder.index.to_list()
away_defender_indexes = train_away_defender.index.to_list()
away_goalkeeper_indexes = train_away_goalkeeper.index.to_list()

expected_indexes = [i for i in range(0, len(train_home))]

nb_variables = train_home_attacker.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in home_attacker_indexes:
        train_home_attacker.loc[index] = row_to_insert
train_home_attacker.sort_index(inplace=True)

nb_variables = train_home_midfielder.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in home_midfielder_indexes:
        train_home_midfielder.loc[index] = row_to_insert
train_home_midfielder.sort_index(inplace=True)

nb_variables = train_home_defender.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in home_defender_indexes:
        train_home_defender.loc[index] = row_to_insert
train_home_defender.sort_index(inplace=True)

nb_variables = train_home_goalkeeper.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in home_goalkeeper_indexes:
        train_home_goalkeeper.loc[index] = row_to_insert
train_home_goalkeeper.sort_index(inplace=True)

nb_variables = train_away_attacker.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in away_attacker_indexes:
        train_away_attacker.loc[index] = row_to_insert
train_away_attacker.sort_index(inplace=True)

nb_variables = train_away_midfielder.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in away_midfielder_indexes:
        train_away_midfielder.loc[index] = row_to_insert
train_away_midfielder.sort_index(inplace=True)

nb_variables = train_away_defender.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in away_defender_indexes:
        train_away_defender.loc[index] = row_to_insert
train_away_defender.sort_index(inplace=True)

nb_variables = train_away_goalkeeper.shape[1]
row_to_insert = [np.NaN for i in range(0, nb_variables)]
for index in expected_indexes:
    if index not in away_goalkeeper_indexes:
        train_away_goalkeeper.loc[index] = row_to_insert
train_away_goalkeeper.sort_index(inplace=True)

In [501]:
train_data_players =  pd.concat([train_home_attacker, 
                                 train_home_midfielder, 
                                 train_home_defender, 
                                 train_home_goalkeeper,
                                 train_home_all_players, 
                                 train_away_attacker, 
                                 train_away_midfielder, 
                                 train_away_defender, 
                                 train_away_goalkeeper, 
                                 train_away_all_players],join='inner',axis=1)

train_data_players = train_data_players.replace({np.inf:np.nan,-np.inf:np.nan})

In [502]:
train_data_players

HOME_ATTACKER_ACCURATE_CROSSES_season_sum  \
ID                                                 
0                                            NaN   
1                                            NaN   
2                                      13.829268   
3                                       3.294118   
4                                      20.904059   
...                                          ...   
12298                                        NaN   
12299                                   0.231343   
12300                                        NaN   
12301                                        NaN   
12302                                   5.931429   

       HOME_ATTACKER_ACCURATE_PASSES_season_sum  \
ID                                                
0                                           NaN   
1                                           NaN   
2                                     12.475610   
3                                     15.367647   
4                                     22.431734   
...                                         ...   
12298                                       NaN   
12299                                 12.567164   
12300                                       NaN   
12301                                       NaN   
12302                                 15.554286   

       HOME_ATTACKER_AERIALS_WON_season_sum  HOME_ATTACKER_ASSISTS_season_sum  \
ID                                                                              
0                                       NaN                               NaN   
1                                       NaN                               NaN   
2                                 18.146341                          5.207317   
3                                 11.198529                         12.639706   
4                                 18.169742                         27.516605   
...                                     ...                               ...   
12298                                   NaN                               NaN   
12299                             47.156716                          8.835821   
12300                                   NaN                               NaN   
12301                                   NaN                               NaN   
12302                             15.834286                         48.091429   

       HOME_ATTACKER_BIG_CHANCES_CREATED_season_sum  \
ID                                                    
0                                               NaN   
1                                               NaN   
2                                         10.243902   
3                                          7.058824   
4                                         34.837638   
...                                             ...   
12298                                           NaN   
12299                                      6.074627   
12300                                           NaN   
12301                                           NaN   
12302                                     35.622857   

       HOME_ATTACKER_BIG_CHANCES_MISSED_season_sum  \
ID                                                   
0                                              NaN   
1                                              NaN   
2                                        20.841463   
3                                        34.654412   
4                                        26.022140   
...                                            ...   
12298                                          NaN   
12299                                    23.507463   
12300                                          NaN   
12301                                          NaN   
12302                                    27.748571   

       HOME_ATTACKER_BLOCKED_SHOTS_season_sum  \
ID                                              
0                                         NaN   
1                                         NaN 

#### GATHERING DATA

In [503]:
train_data =  pd.concat([train_data_teams,train_data_players],join='inner',axis=1)

In [504]:
train_data

HOME_TEAM_SHOTS_TOTAL_season_sum  HOME_TEAM_SHOTS_INSIDEBOX_season_sum  \
ID                                                                              
0                                   3.0                                   2.0   
1                                   6.0                                   8.0   
2                                   4.0                                   2.0   
3                                   7.0                                   5.0   
4                                   3.0                                   3.0   
...                                 ...                                   ...   
12298                               4.0                                   2.0   
12299                               4.0                                   2.0   
12300                               4.0                                   3.0   
12301                               2.0                                   NaN   
12302                               2.0                                   3.0   

       HOME_TEAM_SHOTS_OFF_TARGET_season_sum  \
ID                                             
0                                        5.0   
1                                        3.0   
2                                        5.0   
3                                        5.0   
4                                        2.0   
...                                      ...   
12298                                    3.0   
12299                                    3.0   
12300                                    5.0   
12301                                    1.0   
12302                                    1.0   

       HOME_TEAM_SHOTS_ON_TARGET_season_sum  \
ID                                            
0                                       2.0   
1                                       6.0   
2                                       2.0   
3                                       6.0   
4                                       3.0   
...                                     ...   
12298                                   4.0   
12299                                   1.0   
12300                                   3.0   
12301                                   1.0   
12302                                   2.0   

       HOME_TEAM_SHOTS_OUTSIDEBOX_season_sum  HOME_TEAM_PASSES_season_sum  \
ID                                                                          
0                                        1.0                          2.0   
1                                        5.0                          8.0   
2                                        8.0                          1.0   
3                                        6.0                          9.0   
4                                        4.0                          4.0   
...                                      ...                          ...   
12298                                    7.0                          4.0   
12299                                    5.0                          1.0   
12300                                    5.0                          1.0   
12301                                    NaN                          NaN   
12302                                    2.0                          3.0   

       HOME_TEAM_SUCCESSFUL_PASSES_season_sum  HOME_TEAM_SAVES_season_sum  \
ID                                                                          
0                                         2.0                         5.0   
1                                         7.0                        10.0   
2                                         1.0                         2.0   
3                                         9.0                         2.0   
4                                         3.0                         4.0   
...                                       ...                         ...   
12298                                     4.0                         3.0   
12299                

#### BENCHMARK

In [505]:
# predicting if away wins
train_new_y = train_scores['AWAY_WINS']

In [506]:
# splitting train/test
X_train, X_test, y_train, y_test = model_selection.train_test_split(train_data, train_new_y, train_size=0.8, random_state=42)
X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, train_size=0.8, random_state=42)

In [507]:
# XGB model

params_1 = {
    'booster': 'gbtree',
    'tree_method':'hist',
    'max_depth': 8, 
    'learning_rate': 0.025,
    'objective': 'multi:softprob',
    'num_class': 2,
    'eval_metric':'mlogloss'
    }


d_train = xgb.DMatrix(X_train.replace({0:np.nan}), y_train)
d_valid = xgb.DMatrix(X_valid.replace({0:np.nan}), y_valid)

num_round = 10000
evallist = [(d_train, 'train'), (d_valid, 'eval')]

bst = xgb.train(params_1, d_train, num_round, evallist, early_stopping_rounds=100)

[0]	train-mlogloss:0.68193	eval-mlogloss:0.68790
[1]	train-mlogloss:0.67129	eval-mlogloss:0.68296
[2]	train-mlogloss:0.66139	eval-mlogloss:0.67856
[3]	train-mlogloss:0.65150	eval-mlogloss:0.67433
[4]	train-mlogloss:0.64246	eval-mlogloss:0.67018
[5]	train-mlogloss:0.63383	eval-mlogloss:0.66589
[6]	train-mlogloss:0.62494	eval-mlogloss:0.66195
[7]	train-mlogloss:0.61615	eval-mlogloss:0.65778
[8]	train-mlogloss:0.60823	eval-mlogloss:0.65418
[9]	train-mlogloss:0.60077	eval-mlogloss:0.65041
[10]	train-mlogloss:0.59337	eval-mlogloss:0.64712
[11]	train-mlogloss:0.58630	eval-mlogloss:0.64387
[12]	train-mlogloss:0.57890	eval-mlogloss:0.64054
[13]	train-mlogloss:0.57186	eval-mlogloss:0.63763
[14]	train-mlogloss:0.56486	eval-mlogloss:0.63450
[15]	train-mlogloss:0.55857	eval-mlogloss:0.63163
[16]	train-mlogloss:0.55218	eval-mlogloss:0.62919
[17]	train-mlogloss:0.54589	eval-mlogloss:0.62673
[18]	train-mlogloss:0.53981	eval-mlogloss:0.62456
[19]	train-mlogloss:0.53357	eval-mlogloss:0.62210
[20]	train